# 3D Geometries in netgen.occ

We recommend now moving from the old CSG modeling in Netgen to the Python - Opencascade one. All CSG functionality is available here as well and way more.
Netgen provides a Python wrapper around the Open Cascade Technology (OCCT) geometry kernel. It allows to model complex geometric objects. It also allows to import models via STEP format, explore, and modify the geometry. For that geometry type you have to install Netgen with the cmake-flag -DUSE_OCC=ON (or with any of the available installers).

In the wrapper we aim in bringing most of the structure of OCCT to Python. If you are familiar with the C++ interface of Open Cascade you will recognize many classes. 

## Construction of 3D objects

You can define your Geometry using Primitives and boolearn operations on them

| Syntax | Explanation |
|------|-------------|
|Box((x1,y1,z1),(x2,y2,z2)) | Orthobrick with min and max Point |
|Sphere(c, r) | Sphere with center and radius |
| HalfSpace(p, v) | Halfspace with given point and normal vector |
|Cylinder(c, dir, r, h, bot=None, top=None, mantle=None) | Cylinder with center c, axis direction dir, <br/> radius r, height h, boundary names can be optionally given |
| Ellipsoid(Axes(p, n, vx), r1, r2, r3=r2) | Ellipsoid with center p, r3 axis n and r1 axis vx |
| Cone(gp_Ax2(p, d), r1, r2, h) | Cone with center p and direction d, r1 is radius at p, <br/> r2 radius at p + hd |

Operations to modify shapes:

| Operation | Explanation |
|-|-|
| a * b | Common part of two shapes |
| a + b | Unify a and b (one domain afterwards) |
| Glue([a,b]) | Glue a and b together (separate domains with common interface) |
| a - b | a without b |
| Compound([a,b], separate_layers=False) | Separate domains with separate interface (even when touching/overlapping) <br/> Use separate layers to have meshsize restrictions on one body not apply for the other one |
| Revolve(face, Axis(p, d), D) | Revolve the face around the axis for D degrees |
| Pipe(spine, profile, twist, auxspine) | A pipe is built a basis shape (called the profile) along a wire (called the spine) by sweeping. <br/> The profile must not contain solids. |
| Extrude(face, h, dir=Z, idenfity=False, <br/> idtype=IdentificationType.CLOSE_SURFACES, idname="extrusion") | Extrude face in direction dir and with height h.<br/> If identify is true identify the resulting faces, per default with closesurface identification |

We define a box aligned with the Cartesian coordinates given by two points with minimal and maximal x/y/z coordinates. A cylinder is given by a point on the axis, a direction vector, the radius r, and the height h. The symbols X, Y, and Z are predefined basis vectors for the Cartesian coordinates.

In [ ]:
from netgen.occ import *
from ngsolve import Mesh
from ngsolve.webgui import Draw

In [ ]:
box = Box(Pnt(0,0,0), Pnt(1,1,1))
cyl = Cylinder(Pnt(1,0.5,0.5), X, r=0.3, h=0.5)

The Boolean operations fuse, common, and cut provided by OCCT are made available by the operators +, * and -. More can be found in the OCCT-documentation. Note that the fuse generates one new solid, there is no interface face where the cylinder is touching the box.

In [ ]:
fused = box + cyl
Draw(fused, clipping=True)

For mesh generation, we make a Netgen OCC-Geometry from the OCC-shape. Then we can call the Netgen mesh generation as usual:

In [ ]:
geo = OCCGeometry(fused)
mesh = Mesh(geo.GenerateMesh(maxh=0.2))
mesh.Curve(3)
Draw (mesh, clipping=True);

Instead of fusing, we can glue together shapes. Then, the resulting composite solid contains the interface face between the solids. This is important when dealing with separate material regions:

In [ ]:
geo = Glue( [box, cyl])
Draw(geo, clipping=True)

mesh = Mesh(OCCGeometry(geo).GenerateMesh(maxh=0.2)).Curve(3)
Draw(mesh, clipping=True);

A third option is to form a compound of shapes, then the component shapes are meshed independently:

In [ ]:
geo = Compound( [box, cyl])
Draw(geo, clipping=True)

mesh = Mesh(OCCGeometry(geo).GenerateMesh(maxh=0.2)).Curve(3)
Draw (mesh, clipping=True);

## Transformation of shapes

We can translate, rotate and mirror shapes. The transformation preserves the original shape, and returns a transformed copy. The translation Move takes a vector as argument, the rotation Rotation needs an axis given by a point and a direction, and an angle. The sign of the angle reflects the right hand screw rule.

In [ ]:
solid = Box((0,0,0), (5,3,1)) + Sphere((0,0,0), 0.3)
solid2 = solid.Move((5,0,2))
solid3 = solid.Move((0,0,4)).Rotate( Axis((0,0,4), X), 45)
Draw(solid + solid2 + solid3);

# Hierarchy of shapes
OCCT keeps track of the hierarchy of shapes. A solid knows its faces, a face its edges, and a edge its vertices. We can ask a shape for a list of sub-shapes.

In [ ]:
solid = Box((0,0,0), (1,1,1))
explodedF = sum( [f.Move(0.2 * (f.center-(0.5, 0.5, 0.5))) for f in solid.faces] )
explodedE = sum( [e.Move(0.2 * (e.center-(0.5, 0.5, 0.5))) for e in solid.edges] )

Draw( Compound( [explodedF, explodedE] ) );

In [ ]:
for f in solid.faces:
    print ("center of gravity", f.center)

In [ ]:
e = solid.edges[0]
print ("I am a", e.type)
print ("with startpoint", e.start, "and endpoint", e.end)

In [ ]:
for f in solid.faces:
    print ("face")
    for e in f.edges:
        print ("edge:", e.start, "-", e.end)

## Properties of shapes

Each shape (Solid, Face, Edge, Vertex) can have the following properties set:

| Property | Value Type | Meaning |
|-|-|-|
| name | str | name of the shape |
| maxh | float | Local meshsize restriction of the shape |
| layer | int | Meshing layer of the shape |
| col | tuple[float, float, float, optional[float]] | Color of the shape (r,g,b,a=1), currently only used for faces |

Transparency is not (yet) supported in the webgui, the Netgen gui does support it.

Layer usually only makes sense for the highest dimensional shapes (solid in 3d and face in 2d). Netgen creates a meshsize tree for each layer for meshing, meaning that local meshsize restrictions of objects in different layers do not influence each other.

These properties can also be directly assigned to a `ListOfShapes` that is returned by the `.solids`, `.faces`, `.edges` and `.vertices` properties of shapes.

In [ ]:
solid.faces.col = (1,0,0)
Draw(solid)

## Selection of shapes

Sometimes we want to set properties of shapes, boundary conditions or mesh-size. For that we can use shape selectors.

The Max and Min selectors finds the sub-shapes where the center of gravity has maximal or minimal coordinates in a given direction

<div class="alert alert-block alert-warning"><b>Warning:</b> Min and Max operator return only one shape! So if multiple shapes do have their center in the same plane it will return one arbitrary of them. </div>

In [ ]:
solid.faces.Min(X).col = (0,0,1)
solid.faces.Max(X).name = "right"
# Draw(solid)

two_boxes = Glue([solid, solid.Move((0,0,1))])
two_boxes.faces.Max(X).col = (1,1,0)
two_boxes.faces.Max(X).name = "maxX"
Draw(two_boxes)


To get all faces in the `x == 1` plane the `shape.[]` operator can be used. It takes as input a `netgen.occ.DirectionalInterval` which can be created by comparing `netgen.occ.Vec3` with values:

The operator returns all shapes where the center lies in the given interval.

In [ ]:
two_boxes.faces[X>=1][Z<1].col = (0,1,1)
two_boxes.faces[X>=1][Z<=1].name = "lower_right"
Draw(two_boxes)

Shape names can later also be used to access the subshapes:

In [ ]:
two_boxes.faces["lower_right"].maxh = 0.1
mesh = Mesh(OCCGeometry(two_boxes).GenerateMesh())
Draw(mesh)

Netgen also provides operators to combine list of shapes:

| Syntax | Meaning |
| - | - |
| a * b | Common subshapes |
| a + b | Sum of subshapes |

This can, for example be used to reduce the meshsize on the edge between two faces:

In [ ]:
(two_boxes.faces["left|right"].edges * two_boxes.faces["lower_right"].edges).maxh = 0.05
mesh = Mesh(OCCGeometry(two_boxes).GenerateMesh())
Draw(mesh)

## Periodic and closesurface identification

Periodic and closesurface identifications work the same as in 2D.

One pitfall is having to have symmetric geometry boundaries. For example here identification does not work:

In [ ]:
outer = Box((0,0,0),(3,3,3))
metal = Box((0,0,0), (1,1,1))
metal.solids.name = "metal"
air = outer - metal
air.solids.name = "air"
shape = Glue([metal, air])
trafo = gp_Trsf.Translation(3 * X)
shape.faces[X<=0].Identify(shape.faces[X>=3], "periodic", IdentificationType.PERIODIC, trafo)
geo = OCCGeometry(shape)
mesh = Mesh(geo.GenerateMesh(maxh=0.5))
Draw(mesh)

A trick to make this work is to glue the edges into the other side to make the shape periodic:

In [ ]:
shape = Glue([shape, trafo(Glue(shape.faces[X<=0].edges))])
Draw(shape)

In [ ]:
shape.faces[X<=0].Identify(shape.faces[X>=3], "periodic", IdentificationType.PERIODIC, trafo)
geo = OCCGeometry(shape)
mesh = Mesh(geo.GenerateMesh(maxh=0.5))

# Code to draw identifications
plist = []
for pair in mesh.ngmesh.GetIdentifications():
    plist += list(mesh.vertices[pair[0]-1].point)
    plist += list(mesh.vertices[pair[1]-1].point)
Draw(mesh, objects=[{"type" : "lines", "position" : plist, "name": "identification", "color": "purple"}])